# 1. 基于 MaxFrame 实现分布式 Pandas 处理

## 1.1 MaxFrame 介绍

在数据科学领域，提升数据处理和分析的效率至关重要。Python 凭借其丰富的第三方库（如 NumPy、Pandas 和 Scikit-learn）在数据科学中提供了强大支持，但其单机计算能力往往难以满足大数据处理需求。

为解决这一问题，MaxCompute 提供了分布式计算框架 MaxFrame。它兼容 Python 编程接口，并利用 MaxCompute 的弹性计算资源和海量数据，实现自动分布式计算。用户可以在 MaxCompute 上高效进行大规模数据分析、数据探索和 AI 开发。

想要详细了解 MaxFrame 的能力和使用可以参考如下文档：

* [MaxFrame 官网介绍](https://www.aliyun.com/product/bigdata/odps/maxframe?spm=5176.7944453.J_5834642020.5.591a5d53jEGdCZ)

* [MaxFrame 用户文档](https://help.aliyun.com/zh/maxcompute/user-guide/maxframe/?spm=a2c4g.11186623.0.0.2f927822OvdDLA)

* [MaxFrame 开发手册](https://maxframe.readthedocs.io/en/latest/user_guide/index.html)

## 1.2 场景说明

本文将带您了解 MaxFrame 开发的基本流程，并通过一个商品和销售的案例带您了解如何通过 MaxFrame 使用与 Pandas 兼容的 API 进行分布式数据处理。

# 2. 准备环境和数据

## 2.1 准备项目

在开始之前，您需要准备 MaxCompute 项目，用于后续计算。

如果您不清楚如何创建 MaxCompute 项目或尚未创建，可点击以下链接跳转至 MaxCompute 项目管理页面：
- 获取 MaxCompute 项目名：您可以登录 [MaxCompute 控制台](https://maxcompute.console.aliyun.com/)，在左侧导航栏选择工作区 > 项目管理，查看 MaxCompute 项目名称。
- Endpoint：目标 MaxCompute 项目所在地域的 Endpoint，可根据网络连接方式自行选择，例如 http://service.cn-chengdu.maxcompute.aliyun.com/api。详情请参见 [获取 Endpoint](https://help.aliyun.com/document_detail/34951.htm?spm=a2c4g.53056.0.0.25986d7eQ1nIyQ#concept-m2j-h1y-5db)。

In [1]:
PROJECT_NAME = "[your-project-name]" #请将 [your-project-name] 替换为您的项目名

## 2.2 准备数据

创建本示例所需的小规模测试数据。脚本中使用的 API 不是本教程的重点，仅用于创建和生成测试数据，您可以忽略其中的细节。

In [2]:
import os
import pandas as pd
import numpy as np
from odps import ODPS
from odps.df import DataFrame as ODPSDataFrame

# 创建 odps 对象
o = ODPS(
    project=PROJECT_NAME,
    endpoint=os.getenv('ODPS_ENDPOINT'),
    tunnel_endpoint = os.getenv('ODPS_TUNNEL_ENDPOINT')
)

# 测试数据
data_sets = [
    {
        "table_name": "product",
        "table_schema": "index bigint, product_id bigint, product_name string, current_price bigint",
        "source_type": "records",
        "records": [
            [1, 100, "Nokia", 1000],
            [2, 200, "Apple", 5000],
            [3, 300, "Samsung", 9000],
            [4, 500, "HP", 7000],
        ],
        "lifecycle": 5,
    },
    {
        "table_name": "sales",
        "table_schema": "index bigint, sale_id bigint, product_id bigint, user_id bigint, year bigint, quantity bigint, price bigint",
        "source_type": "records",
        "records": [
            [1, 1, 100, 101, 2008, 10, 5000],
            [2, 2, 300, 101, 2009, 7, 4000],
            [3, 4, 100, 102, 2008, 9, 4000],
            [4, 5, 200, 102, 2010, 6, 6000],
            [5, 8, 300, 102, 2008, 10, 9000],
            [6, 9, 100, 102, 2009, 6, 2000],
            [7, 13, 500, 104, 2007, 3, 8000],
        ],
        "lifecycle": 5,
    },
]

# 创建表
def prepare_data(o: ODPS, data_sets, suffix="", drop_if_exists=False):
    for index, data in enumerate(data_sets):
        table_name = data.get("table_name")
        table_schema = data.get("table_schema")
        source_type = data.get("source_type")

        if not table_name or not table_schema or not source_type:
            raise ValueError(
                f"Dataset at index {index} is missing one or more required keys: 'table_name', 'table_schema', or 'source_type'."
            )

        lifecycle = data.get("lifecycle", 5)
        table_name += suffix

        print(f"Processing {o.project}.{table_name}...")
        if drop_if_exists:
            print(f"Deleting {o.project}.{table_name} if exists...")
            o.delete_table(table_name, if_exists=True)

        o.create_table(
            name=table_name,
            table_schema=table_schema,
            lifecycle=lifecycle,
            if_not_exists=True,
        )

        if source_type == "local_file":
            file_path = data.get("file")
            if not file_path:
                raise ValueError(
                    f"Dataset at index {index} with source_type 'local_file' is missing the 'file' key."
                )
            sep = data.get("sep", ",")
            pd_df = pd.read_csv(file_path, sep=sep)
            ODPSDataFrame(pd_df).persist(table_name, drop_table=True)

        elif source_type == "records":
            records = data.get("records")
            if not records:
                raise ValueError(
                    f"Dataset at index {index} with source_type 'records' is missing the 'records' key."
                )
            with o.get_table(table_name).open_writer() as writer:
                writer.write(records)
        else:
            raise ValueError(f"Unknown data set source_type: {source_type}")

        print(f"Processed {o.project}.{table_name} Done")


prepare_data(o, data_sets, "_maxframe_demo", True)

Processing maxframe_hk.product_maxframe_demo...
Deleting maxframe_hk.product_maxframe_demo if exists...
Processed maxframe_hk.product_maxframe_demo Done
Processing maxframe_hk.sales_maxframe_demo...
Deleting maxframe_hk.sales_maxframe_demo if exists...
Processed maxframe_hk.sales_maxframe_demo Done


# 3. 使用 MaxFrame 进行数据分析

## 3.1 会话初始化

MaxFrame 依赖于 MaxCompute 的资源来执行计算，因此首先需要建立一个 MaxCompute 会话。`new_session` 是 MaxFrame 创建会话的入口。在创建会话之后，所有后续的计算都将默认使用该会话进行通信。MaxFrame 会在远端保存中间状态，因此你可以进行交互式操作，一边开发一边验证。

在创建完成后，可以从 session 对象中获得 `session_id` 和 `logview_address`，前者是该会话的唯一 id，后者是用于查看在该 session 中产生的所有计算的作业执行情况。

In [3]:
from maxframe.session import new_session
import maxframe.dataframe as md

# 初始化 MaxFrame Session
session = new_session(o)

# 打印 Session ID
print(f"MaxFrame Session ID: {session.session_id}")

# 打印 LogView 地址
print(f"MaxFrame LogView 地址: {session.get_logview_address()}")

MaxFrame Session ID: 20240722073557586g5ieim1e2tp5
MaxFrame LogView 地址: http://logview.odps.aliyun.com/logview/?h=http://service-internal.cn-hongkong.maxcompute.aliyun-inc.com:8090/api&p=maxframe_hk&i=20240722073557586g5ieim1e2tp5&token=VVErZExQTldxSjA4QkRwaGFHc0k3bXJoTWxrPSxPRFBTX09CTzo1NTI3MDE1NDY5MDc1Nzg4LDE3MjE2NTAzMDUseyJWZXJzaW9uIjogIjEiLCAiU3RhdGVtZW50IjogW3siQWN0aW9uIjogWyJvZHBzOioiXSwgIlJlc291cmNlIjogImFjczpvZHBzOio6KiIsICJFZmZlY3QiOiAiQWxsb3cifV0sICJPcmlnaW5hbENvbnRleHQiOiB7ImFjczpTb3VyY2VJcCI6IjEwLjE2LjM5LjEzNSIsIngtdnBjb3B0LWFkZHIiOiIyNzU2NDI3NTMxIiwieC12cGNvcHQtaWQiOiIwIiwieC12cGNvcHQtcG9ydCI6IjM5NDU1IiwieC12cGNvcHQtdmVyaWZ5IjoieWVzIiwieC12cGNvcHQtdnBjaWQiOiIifX0=


## 3.2 数据探查

本次演示的场景是使用 MaxFrame 对商品和销售数据进行分析。这些数据统一存储于两张 MaxCompute 数据表中：商品表包含商品、价格等信息；销售表包含客户、产品、销售数量、销售年份、销售价格等信息。

| MaxCompute 表 | 描述                                             |
| ------------- | -----------------------------------------------  |
| Product       | 商品维度表，包含商品名称、价格等                  |
| Sales         | 销售事实表，包含销售的商品 ID、售出年份、数量、价格等 |

与 Pandas 一样，在获得 dataframe 对象之后，您可以使用 `dtypes` 来查看数据的 schema。在下例中，[md.read_odps_table](https://help.aliyun.com/zh/maxcompute/user-guide/data-input-and-output) 会获得 `maxframe.DataFrame` 对象。

In [4]:
print('--------------Product Table Schema-----------------------')
product = md.read_odps_table("product_maxframe_demo", index_col="product_id")
print(product.dtypes)

print('\n--------------Sales Table Schema-----------------------')
sales = md.read_odps_table("sales_maxframe_demo", index_col="index")
print(sales.dtypes)

--------------Product Table Schema-----------------------
index             int64
product_name     object
current_price     int64
dtype: object

--------------Sales Table Schema-----------------------
sale_id       int64
product_id    int64
user_id       int64
year          int64
quantity      int64
price         int64
dtype: object


在 MaxFrame 中，DataFrame 可以使用与 Pandas 兼容的接口进行计算，例如下例中的 `head`。但与 Pandas 不同的是，MaxFrame 中的数据并不存储在本地。MaxFrame 通过 Lazy 计算使你可以在本地使用各种算子，并通过 `execute()` 来触发计算一并提交到 MaxCompute 集群中分布式执行。

MaxFrame 已经对 Notebook 进行了适配，在 `execute()` 之后能够高效预览 MaxCompute 中数据的首末数行。

In [5]:
sales.head(5).execute()

100%|██████████| 100.00/100 [00:10<00:00,  9.81it/s] 


sale_id  product_id  user_id  year  quantity  price
index                                                     
1            1         100      101  2008        10   5000
2            2         300      101  2009         7   4000
...        ...         ...      ...   ...       ...    ...
4            5         200      102  2010         6   6000
5            8         300      102  2008        10   9000

[nan rows x 5 columns]

## 3.3 数据分布式处理

利用 MaxFrame 的功能，我们能够使用与 **Pandas 兼容**的语法进行数据分析。所有算子的设计均为 **分布式执行**，确保计算的高效性。
相比于单机 Pandas，MaxFrame 的 Pandas 算子运行在 MaxCompute 计算集群中，能够大规模并行处理数据，数据读取效率也明显优于单机 Pandas。

我们将展示两个与 MaxFrame 分布式 Pandas 算子相关的数据处理场景。

### 3.3.1 场景 1：Pandas merge接口的分布式执行
连接两张数据表，以获取 product_maxframe_demo_large 表中所有 sale_id 对应的 product_name 以及该产品的所有 year 和 price

In [ ]:
# 默认打印 Logview 信息
import logging
logging.basicConfig(level=logging.INFO)

sales = md.read_odps_table("sales_maxframe_demo", index_col="index")
product = md.read_odps_table("product_maxframe_demo", index_col="product_id")

# 这里的df并不会立即执行，除非您使用df.execute()来触发。
# 这意味着所有的计算都将最终完全在MaxCompute集群完成，避免了中间所不必要的数据传输和阻塞。
df = sales.merge(product, left_on="product_id", right_index=True)
df = df[["product_name", "year", "price"]]

execute_result = df.execute()

  0%|          |   0.00/100 [00:09<?, ?it/s]

`df.execute()` 会触发在 MaxCompute 集群上进行分布式计算，您可以在 Logview 中查看当前计算的执行详情。

在内部测试中，Product 和 Sales 两张数据表的 6.8TB 数据在 MaxFrame 的 merge 算子中仅需 3 分钟即可完成计算。相比之下，在本地使用 Pandas 处理 6.8TB 的数据会超出内存限制，无法执行。

![merge Operator](./images/merge_operator.png)

如果您想在本地查看所有计算结果，可以使用 `fetch()` 方法将所有结果提取到本地进行查看。

In [8]:
execute_result.fetch()

product_name  year  price
index                          
1            Nokia  2008   5000
2          Samsung  2009   4000
3            Nokia  2008   4000
4            Apple  2010   6000
5          Samsung  2008   9000
6            Nokia  2009   2000
7               HP  2007   8000

### 3.3.2 场景 2：Pandas groupby、agg、sort_values 接口的分布式执行
连接 Product 和 Sales 两张数据表，聚合每个产品在 Sales 表中的首次售出年份。

In [9]:
# 聚合每个产品的首次售出年份
min_year_df = md.read_odps_table("sales_maxframe_demo", index_col="index")
min_year_df = min_year_df.groupby('product_id', as_index=False).agg(first_year=('year', 'min'))

# 计算不同首次售出年份的产品 ID 数量
sum_product_min_year_df = min_year_df.groupby('first_year', as_index=False).agg(total_product_num=('product_id', 'count'))
exe_info = sum_product_min_year_df.execute()

INFO:maxframe_client.session.odps:Session ID: 20240702065644804gijhe4ezawr3, DAG ID: 3bc3551eee2b4e4faaf52432e40a6670, Logview: http://logview.odps.aliyun.com/logview/?h=http://service.cn-beijing.maxcompute.aliyun.com/api&p=maxframe_test_bj&i=20240702065644804gijhe4ezawr3&token=V29VUGhOK2dSQllJM1RlZ1lISWRKWDd4VGFBPSxPRFBTX09CTzoxNDY0NzgzMTkzMDA5OTMxLDE3MjUwODc0MDkseyJTdGF0ZW1lbnQiOlt7IkFjdGlvbiI6WyJvZHBzOlJlYWQiXSwiRWZmZWN0IjoiQWxsb3ciLCJSZXNvdXJjZSI6WyJhY3M6b2RwczoqOnByb2plY3RzL21heGZyYW1lX3Rlc3RfYmovaW5zdGFuY2VzLzIwMjQwNzAyMDY1NjQ0ODA0Z2lqaGU0ZXphd3IzIl19XSwiVmVyc2lvbiI6IjEifQ==&dagId=3bc3551eee2b4e4faaf52432e40a6670


  0%|          |   0.00/100 [00:00<?, ?it/s]

INFO:odps.tunnel.tabletunnel:Tunnel session created: <TableDownloadSession id=20240702145855c2c7dc0b0086f599 project=maxframe_test_bj table=tmp_mf_20240702065644804gijhe4ezawr3_ec29bf8468f83499d2fc7f5c6072fca6_0 partition_spec=None>


在执行完上述分布式计算后，如果本地内存允许，您可以对 `execute()` 的结果使用 `fetch()` 将结果拉全部取到本地使用，抓取后的数据会形成 Pandas DataFrame，因此对于 MaxFrame 尚无法支持的场景您也可以轻松的和本地的工作流结合。

当然您需要考虑取数的耗时、带宽和本地内存的限制，我们推荐您尽可能的在远端完成所有的计算，避免频繁的抓取和上传。

In [10]:
local_df = exe_info.fetch().head(10)
local_df

first_year  total_product_num
0        2007                  1
1        2008                  2
2        2010                  1

在提取并展示了记录后，您还可以使用 Matplotlib 生成图表来可视化数据。以下是一个示例代码，用于绘制每个首次售出年份的产品数量分布图。

In [11]:
import matplotlib.pyplot as plt

plt.plot(local_df['first_year'],local_df['total_product_num'])
plt.xlabel('First_sale_year')
plt.ylabel('Total_product_num')
plt.title('Saled product distribution by first saled year')
plt.xticks(range(int(local_df['first_year'].min()), int(local_df['first_year'].max()) + 1))
plt.show()

## 3.4 释放资源

在所有计算完成后，请确保使用 `destroy()` 方法来销毁会话，以释放资源。

In [12]:
session.destroy()